To get started with pyGSTi (https://github.com/sandialabs/pyGSTi), the complete local installation is recommended (check installation instructions on Github and make sure to have c++ build tools installed). Start with the Essential objects notebook tutorial and move on from there. When simulating data, the necessary objects to use are ProcessorSpec, Model (cloud crosstalk if you want to model crosstalk errors), Circuit, CircuitList and DataSet. The tutorials cover each of these very well.

The next cell contains necessary functions to make pyGSTi's deprecated crosstalk detection functions work. The first one was in the library but needed some changes to work (changed or added lines denoted by #####) and the remaining ones are my own. Execute and move on (importing pygsti takes around 10 seconds). Works in version 0.9.12.3.

In [ ]:
import numpy as np
import pygsti
from pygsti.circuits import Circuit
import qiskit
from qiskit import QuantumCircuit

def axel_crosstalk_detection_experiment2(pspec, lengths, circuits_per_length, circuit_population_sz, multiplier=3,
                                    idle_prob=0.1, structure='1Q',
                                    descriptor='A set of crosstalk detections experiments', verbosity=1):
	"""
	Modified from the original and deprecated pyGSTi function "crosstalk_detection_experiment2()", modified or added lines
	are denoted by #####.
	Generates a dictionary that contains information about the experiment, including the generated random circuits.
	"""
	experiment_dict = {}
	experiment_dict['spec'] = {}
	experiment_dict['spec']['lengths'] = lengths
	experiment_dict['spec']['circuit_population_sz'] = circuit_population_sz
	experiment_dict['spec']['multiplier'] = multiplier
	experiment_dict['spec']['idle_prob'] = idle_prob
	experiment_dict['spec']['descriptor'] = descriptor
	experiment_dict['spec']['createdby'] = 'extras.crosstalk.crosstalk_detection_experiment2'
	experiment_dict['spec']["cpl"] = circuits_per_length #####

	if isinstance(structure, str):
		assert(structure == '1Q'), "The only default `structure` option is the string '1Q'"
		structure = tuple([(q,) for q in pspec.qubit_labels])
		n = pspec.num_qubits
	else:
		assert(isinstance(structure, list) or isinstance(structure, tuple)), \
			"If not a string, `structure` must be a list or tuple."
		qubits_used = []
		for subsetQs in structure:
			assert(isinstance(subsetQs, list) or isinstance(subsetQs, tuple)), "SubsetQs must be a list or a tuple!"
			qubits_used = qubits_used + list(subsetQs)
			assert(len(set(qubits_used)) == len(qubits_used)), \
				"The qubits in the tuples/lists of `structure must all be unique!"

		assert(set(qubits_used).issubset(set(pspec.qubit_labels))), \
			"The qubits to benchmark must all be in the QubitProcessorSpec `pspec`!"
		n = len(qubits_used)

	experiment_dict['spec']['circuits_per_length'] = circuits_per_length * multiplier * n

	experiment_dict['spec']['structure'] = structure
	experiment_dict['circuits'] = {}
	experiment_dict['settings'] = {}
	
	experiment_dict["subcircuits"] = {} #####
	experiment_dict['spec']["n"] = n #####

	gates_available = list(pspec.primitive_op_labels)
	gates_by_qubit = [[] for _ in range(0, n)]
	for i in range(0, len(gates_available)):
		for q in range(0, n):
			if gates_available[i].qubits == (q,):
				gates_by_qubit[q].append(gates_available[i])

	for lnum, l in enumerate(lengths):
		# generate menu of circuits for each qubit
		circuit_menu = [[] for _ in range(0, n)]
		for q in range(0, n):
			d = len(gates_by_qubit[q])
			if d**l < circuit_population_sz:
				print(('- Warning: circuit population specified too large for qubit {}'
						' -- there will be redundant circuits').format(q))
			for rep in range(0, circuit_population_sz):
				singleQcirc = []
				for j in range(0, l): #creates an l-length single qubit circuit
					r = np.random.randint(0, d)
					singleQcirc.append(gates_by_qubit[q][r])
				circuit_menu[q].append(singleQcirc)

		cnt = 0
		for q in range(0, n):
			# print('  - Qubit {} = '.format(q))
			# need circuits_per_length number of settings for this qubit
			for j in range(circuits_per_length):
				#  iteratively choose each of the circuits in the menu
				qr = j

				# generate "multiplier" number of random circuits on the other qubits with qr setting
				#  on the central qubit
				for m in range(0, multiplier):
					while True:
						circuit = pygsti.circuits.Circuit(num_lines=0, editable=True)
						settings = {}

						for q1 in range(0, n):
							if q1 == q:
								# the setting for the central qubit is fixed
								r = qr
							else:
								# draw a setting
								r = np.random.randint(0, circuit_population_sz)

							settings[(q1,)] = lnum * (circuit_population_sz + 1) + r + 1
							singleQcircuit = pygsti.circuits.Circuit(num_lines=1, line_labels=[q1], editable=True) #####

							for layer in range(0, l):
								singleQcircuit = singleQcircuit.insert_layer(circuit_menu[q1][r][layer], layer) #####
							
							singleQcircuit.done_editing()
							experiment_dict["subcircuits"][(q, j, m, q1)] = singleQcircuit #####
							circuit = circuit.tensor_circuit(singleQcircuit)
					
						experiment_dict['settings'][l, cnt] = settings
						# for each line, except the central qubit, replace sequence with an idle
						#  independently according to idle_prob
						if idle_prob > 0:
							for q1 in range(0, n):
								if q1 != q:
									idle = bool(np.random.binomial(1, idle_prob))
									if idle:
										circuit.replace_with_idling_line_inplace(q1)
										# Update the setting on that qubit to the idling setting
										#  (denoted by the length index)
										experiment_dict['settings'][l, cnt][(q1,)] = lnum * (circuit_population_sz + 1)
										if verbosity > 0: print('(Idled {}) '.format(q1), end='')

						circuit.done_editing()
						# check whether a duplicate n-qubit circuit was generated and repeat if true as
						# continue jumps back to start of while True loop
						if circuit in list(experiment_dict["circuits"].values()):
							continue
						experiment_dict['circuits'][l, cnt] = circuit
						cnt += 1
						if verbosity > 0: print('{}, '.format(m), end='')
						break # non-duplicate circuit breaks the while loop
							
				if verbosity > 0: print(')')
		print('cnt: {}'.format(cnt))
	return experiment_dict

def replace_gates(circuit_list, target_tuple, gate):
	"""
	For every circuit of circuit_list, replaces the gates on qubits specified by target_tuple with input gate.
	"""
	depth = circuit_list[0].depth # number of layers, constant
	targetAsList = list(target_tuple)

	if len(targetAsList) == 2:		
		for i, circuit in enumerate(circuit_list):
			edCircuit = circuit.copy(editable=True)

			for layer in range(0, depth):
				edCircuit[layer, target_tuple] = (gate, targetAsList[0], targetAsList[1])

			edCircuit.done_editing()
			circuit_list[i] = edCircuit

	elif len(targetAsList) == 1:
		for i, circuit in enumerate(circuit_list):
			edCircuit = circuit.copy(editable=True)

			for layer in range(0, depth):
				edCircuit[layer, targetAsList[0]] = (gate, targetAsList[0])

			edCircuit.done_editing()
			circuit_list[i] = edCircuit

	return circuit_list

def aggregate_labels(n, central_region_size):
	"""
	central_region_size = 1: Generates all the 2^n n-qubit state labels and aggregates their individual qubits'
	outcomes of 0 or 1 into separate dictionary entries. For example, for 2 qubits
	qubit0: {"0":["00","01"],"1":["10","11"]}
	qubit1: {"0":["00","10"],"1":["11","01"]}.

	central_region_size = 2: Does the same for outcomes of 00, 01, 10, 11 for each pair of qubits with the pair
	tuple as dictionary entry.
	"""
	singleQLabels = {}
	nQLabels = []

	for i in range(0, 2**n):
		nQLabel = str(bin(i)[2:].zfill(n))	# generates 0-padded binary numbers corresponding to each state label
		nQLabels.append(nQLabel)

	if central_region_size == 1:		
		for q in range(0, n):
			singleQLabels[q] = {}
			outcomes = ["0", "1"]
			
			for outcome in outcomes:
				singleQLabels[q][outcome] = []

				for label in nQLabels:
					if label[q] == str(outcome):
						singleQLabels[q][str(outcome)].append(label)

	if central_region_size == 2:		
		for qa in range(0, n):
			
			for qb in range(qa, n):
				
				if qa != qb:
					singleQLabels[(qa, qb)] = {}
					singleQLabels[(qb, qa)] = {} # measuring pair (a,b) should be same as (b,a)
					outcomes = ["00", "01", "10", "11"]

					for outcome in outcomes:
						singleQLabels[(qa, qb)][outcome] = []
						singleQLabels[(qb, qa)][outcome] = []

						for label in nQLabels:
							
							if label[qa] == outcome[0] and label[qb] == outcome[1]:
								singleQLabels[(qa, qb)][outcome].append(label)
								singleQLabels[(qb, qa)][outcome].append(label)

	return singleQLabels


def make_regional_datasets2(ctDict, mdl, central_region_size, dataset=None, central_region_tuple=None, circuits_override=None, num_samples=1000):
	"""
	Converts multiqubit datasets into 1 or 2 qubit aggregated datasets specified by central_region_size and -tuple.
	If central_region_tuple=None, for each subcircuit (circuits_per_length in total) on central qubit q it picks the next multiplier number of circuits
	from the circuit list of ctDict, as they are the contexts in which the central subcircuit is run. Then it generates new datasets with measurements
	happening only on the central qubit so that the datasets can be compared later.
	"""
	n = ctDict["spec"]["n"]
	# print("n: ", n)
	multiplier = ctDict["spec"]["multiplier"]
	cpl = ctDict["spec"]["cpl"] # circuits_per_length
	
	if circuits_override == None:
		circuitList = list(ctDict["circuits"].values())
	else:
		circuitList = circuits_override

	for i, circuit in enumerate(circuitList):
		print(i+1)
		print(circuit)

	print("circuits in total: ", len(circuitList))
	# print(circuitList)
	print("single qubit subcircuits in total: ", len(ctDict["subcircuits"]))
	# print(ctDict["subcircuits"])

	singleQLabels = aggregate_labels(n, central_region_size)
	rdsDict = {}

	if central_region_size == 1:
		tempDS = pygsti.data.DataSet(outcome_labels=["0","1"])
		depth = circuitList[0].depth

		for q in range(0, n): # q is the central qubit
			
			for j in range(0, cpl): # circuits_per_length
				
				for m in range(0, multiplier): # multiplier number of contexts for each setting j on central qubit
					
					for q1 in range(0, n):
						
						if q == q1:
							# we want to aggregate the outcomes of the central qubit
							circuitListIndex = q*cpl*multiplier + j*multiplier + m	# slightly demonic looking, but incrementing this nested loop picks the next circuit
							# print("circuitListIndex: ",circuitListIndex)
							multiqCirc = circuitList[circuitListIndex]
							randseed = np.random.randint(1, 1000)
							if dataset == None: # simulates a dataset
								ds = pygsti.data.datasetconstruction.simulate_data(mdl, [multiqCirc], num_samples=num_samples, sample_error='multinomial', seed=randseed, times=[0.0])
							else: # uses the supplied dataset instead
								ds = dataset[multiqCirc]
							
							dsAggre = pygsti.data.datasetconstruction.aggregate_dataset_outcomes(ds, singleQLabels[q])

							dsRow = dsAggre[multiqCirc]

							if circuits_override == None:			
								centralqCirc = ctDict["subcircuits"][(q, j, m, q)] # q1 = q gives settings (subcircuit) on central qubit
							else:
								centralqCirc = pygsti.circuits.Circuit([], line_labels=[q], editable=True)
								trimmedCircuit = multiqCirc.copy(editable=True)
								trimmedCircuit.delete_lines([line for line in range(n) if line != q], delete_straddlers=True)

								for layer in range(0, depth):
									centralqCirc = centralqCirc.insert_layer(trimmedCircuit[layer], layer)

								centralqCirc.done_editing()

							# print("centralqCirc: ", centralqCirc)
							tempDS = pygsti.data.DataSet(outcome_labels=["0","1"])
							tempDS.add_count_dict(centralqCirc, dsRow.counts)

							if centralqCirc in rdsDict:
								rdsDict[centralqCirc].append(tempDS.copy())
							else:
								rdsDict[centralqCirc] = []							
								rdsDict[centralqCirc].append(tempDS.copy())

							print("added to rdsDict[%s]"%str(centralqCirc),"aaa", tempDS)
							break
						
	elif central_region_size == 2:
		tempDS = pygsti.data.DataSet(outcome_labels=["00", "01", "10", "11"])
		depth = circuitList[0].depth

		centralRegion = central_region_tuple	# (qa, qb) tuple, ignoring all other 1q-regions
		CRList = list(centralRegion) # avoiding qubits of central region
		qa = CRList[0]
		qb = CRList[1]
		for j in range(0, cpl): # circuits_per_length
			
			for m in range(0, multiplier): # multiplier number of contexts for each setting j on central qubit
				circuitListIndex = j*multiplier + m
				# print("circuitListIndex: ",circuitListIndex)
				multiqCirc = circuitList[circuitListIndex]
				randseed = np.random.randint(1, 1000)
				ds = pygsti.data.datasetconstruction.simulate_data(mdl, [multiqCirc], num_samples=num_samples, sample_error='multinomial', seed=randseed, times=[0.0])
				# print("ds: ", ds)
				dsAggre = pygsti.data.datasetconstruction.aggregate_dataset_outcomes(ds, singleQLabels[centralRegion])
				# print("dsAggre", centralRegion, ": ", dsAggre)

				dsRow = dsAggre[multiqCirc]				
				centralqCirc = pygsti.circuits.Circuit([], line_labels=[qa, qb], editable=True)
				trimmedCircuit = circuitList[circuitListIndex].copy(editable=True)
				trimmedCircuit.delete_lines([line for line in range(n) if line not in CRList], delete_straddlers=True)

				for layer in range(0, depth):
					centralqCirc = centralqCirc.insert_layer(trimmedCircuit[layer], layer)

				centralqCirc.done_editing()
				# print("centralqCirc: ", centralqCirc)
				tempDS = pygsti.data.DataSet(outcome_labels=["00", "01", "10", "11"])
				tempDS.add_count_dict(centralqCirc, dsRow.counts)

				if centralqCirc in rdsDict:
					rdsDict[centralqCirc].append(tempDS.copy())
				else:
					rdsDict[centralqCirc] = []							
					rdsDict[centralqCirc].append(tempDS.copy())
				# print("added to rdsDict\n[%s]"%str(centralqCirc), tempDS)

	return rdsDict

def compare_datasets(rdsDict):
	"""
	Performs pairwise comparisons between all unique pairs of datasets corresponding to a single central circuit.
	Generates a dictionary where the central circuit is the key whose value is a list of comparator objects.
	Pairwise comparisons are used to get the total variation distance (TVD) in each case.
	For example, given datasets indexed by (0,1,2,3) the unique pairs are (0,1), (0,2), (0,3), (1,2), (1,3), (2,3).
	"""
	centralCircuits = list(rdsDict.keys())
	comparatorDict = {}

	for i in range(0, len(centralCircuits)):
		centralCircuit = centralCircuits[i]
		comparatorDict[centralCircuit] = {}
		dsPairs = []
		comparatorList = []
		indexPairList = []
		length = len(rdsDict[centralCircuit])
		# print(length)

		for j in range(0, length):
			
			for k in range(j+1, length):
				indexPairList.append((j,k))

		# print(indexPairList)

		for indexPair in indexPairList:
			indexList = list(indexPair)
			# dsList = rdsDict[centralCircuits[i]]
			dsList = rdsDict[centralCircuit]
			miniDSList = [dsList[indexList[0]], dsList[indexList[1]]]
			comparator = pygsti.data.DataComparator(miniDSList)
			comparatorList.append(comparator)
			dsPairs.append(miniDSList)
			# comparatorDict[centralCircuit]["ds_pair"] = miniDSList

		
		comparatorDict[centralCircuit]["comparators"] = comparatorList
		comparatorDict[centralCircuit]["ds_pairs"] = dsPairs
		
	# print(comparatorList)
	return comparatorDict

def idle_protocol_crosstalk_experiment(ctDict, protocol="xy"):
	""""
	Implements the XY- and YZ-Idle protocols described in my thesis
	"Device-agnostic crosstalk detection in quantum computers" sections 4.6 and 4.7.
	Replace gates on non-central qubits with idle gates to allow for detection of crosstalk between qubit pairs.
	protocol = "xy": Fails to detect isolated Z-errors, assuming only projective Z-measurement is possible.
	protocol = "yz": replace first and last layers with Ypi/2 rotations on non-central qubits, which
	means Z-evolution from crosstalk or random noise is detectable using a projective Z-measurement.
	"""
	n = ctDict["spec"]["n"]
	multiplier = ctDict["spec"]["multiplier"]
	cpl = ctDict["spec"]["cpl"] # circuits_per_length
	circuitList = list(ctDict["circuits"].values())
	length = circuitList[0].depth
	editedCircuits = circuitList.copy()

	for q in range(0, n):
		for j in range(0, cpl):
			for m in range(0, multiplier):
				for q1 in range(0, n):
					circuitListIndex = q*cpl*multiplier + j*multiplier + m	# slightly demonic looking, but incrementing this nested loop picks the next circuit
					if q1 != q: # replace non-central qubit gates with idles
						tempCircuit = editedCircuits[circuitListIndex].copy(editable=True)
						tempCircuit.replace_with_idling_line_inplace(q1)
						if protocol == "yz": # detects y and z rotations
							tempCircuit[0,q1] = ("Gypi2", q1) # ypi/2 rotation to start
							tempCircuit[length-1,q1] = ("Gypi2", q1) # end with another ypi/2
						tempCircuit.done_editing()
						editedCircuits[circuitListIndex] = tempCircuit
	ctDict["edited_circuits"] = editedCircuits
	return ctDict

def circuits_to_quantumcircuits(ctDict, circuit_list=None, file_name="exported_circuits_q"):
	"""
	Converts the pyGSTi Circuits to Qiskit QuantumCircuits and exports them to qpy files which can be uploaded to Lumi and used in Helmi.
	An output file is generated for each central qubit and one file can contain a maximum of 20 QuantumCircuits.
	Load into Lumi notebook using
	with open("filename", "rb") as handle:
		qcList = qpy.load(handle)
	"""
	n = ctDict["spec"]["n"]
	multiplier = ctDict["spec"]["multiplier"]
	cpl = ctDict["spec"]["cpl"] # circuits_per_length

	if circuit_list == None:
		circuitList = list(ctDict["circuits"].values())
	else:
		circuitList = circuit_list

	if cpl*multiplier > 20:
		print("""Error: You picked over 20 circuits per central qubit, while Helmi supports a maximum of 20 circuits per job.\n
		Please choose circuits_per_length * multiplier <= 20 in axel_crosstalk_detection_experiment2 arguments.\n
		Exiting function...""")
		return None
	
	for q in range(0, n):
		qcList = []
		for j in range(0, cpl):
				for m in range(0, multiplier):
					circuitListIndex = q*cpl*multiplier + j*multiplier + m	# slightly demonic looking, but incrementing this nested loop picks the next circuit
					tempQasm = circuitList[circuitListIndex].convert_to_openqasm(num_qubits=n, include_delay_on_idle=True) # "id" gate is Delay(0), which causes an error on transpilation
					finalQasm = tempQasm.replace("delay(0)", "id") # now it transpiles in Qiskit
					qc = QuantumCircuit(n, n)
					qc = qc.from_qasm_str(finalQasm)
					qcList.append(qc)
		qFileName = file_name + str(q) + ".qpy"
		with open(qFileName, "xb") as file:
			qiskit.qpy.dump(qcList, file)

def aggregate_experimental_idle_protocol_outcomes(counts_dict_list, length, driven_qubits_tuple, protocol="xy", num_qubits=5):
	"""
    Aggregates the Qiskit output counts AROUND the driven qubit into DataSets.
	For example, input a list of of 20 Qiskit counts dictionaries, where q0 was driven
	using 20 gate sequences, with idles on the other qubits. In a system of 5 qubits,
	this function generates 20 aggregated datasets for each spectator qubit (outcomes are "0" or "1",
	read description of aggregate_labels()). Loop over driven qubits in main program if multiple
	counts_dict_lists exist from driving several qubits in turn.
	counts_dict_list: input a list of Qiskit counts dictionaries where only one qubit was driven.
    """
	nQLabels = []
	n = num_qubits
	for i in range(0, 2**n):
		nQLabel = str(bin(i)[2:].zfill(n))	# generates 0-padded binary numbers corresponding to each state label
		nQLabels.append(nQLabel)

	rdsDict = {}
	dQubits = list(driven_qubits_tuple)
	singleQLabels = aggregate_labels(n, 1) # generates a dict of aggregated labels on the central qubit, see description

	for q in range(0, n):
		if q not in dQubits:
			idleCirc = Circuit(line_labels=[q], editable=True, num_lines=1)
			for layerIndex in range(0, length):
				idleCirc = idleCirc.insert_layer(("id", q), layerIndex) # generates an idle circuit on the central qubit
			if protocol == "yz": # detects y and z rotations
				idleCirc[0,q] = ("Gypi2", q) # ypi/2 rotation to start
				idleCirc[length-1,q] = ("Gypi2", q) # end with another ypi/2
			idleCirc.done_editing()
			
			for counts in counts_dict_list:
				counts = {key.replace(key, key[::-1]): value for key, value in counts.items()}	# reverses keys, 
																								# i.e. Qiskit's little endian to conventional big endian (q0 becomes leftmost bit)
				ds = pygsti.data.DataSet(outcome_labels=nQLabels) # generates an empty n-qubit DataSet
				ds.add_count_dict(idleCirc, counts) # adds Qiskit's counts to the DataSet
				dsAggre = pygsti.data.datasetconstruction.aggregate_dataset_outcomes(ds, singleQLabels[q])
				sqtempDS = pygsti.data.DataSet(outcome_labels=["0","1"]) # empty single-qubit dataset
				dsRow = dsAggre[idleCirc] # aggregated counts as if measured on the central qubit only
				sqtempDS.add_count_dict(idleCirc, dsRow.counts)
				if idleCirc in rdsDict:
					rdsDict[idleCirc].append(sqtempDS.copy()) # add single-qubit dataset to list of datasets if the list exists
				else:
					rdsDict[idleCirc] = []
					rdsDict[idleCirc].append(sqtempDS.copy())
	
	return rdsDict

def idle_protocol_crosstalk_simulation(model, ctDict=None, circuits_override=None, num_samples=1000, fixed_seed=None):
	"""
	Simulates the circuits of the XY- or YZ-Idle protocols through circuits_override. Uses a random seed for each circuit simulation
	if fixed_seed!=None.
	"""
	dsList = []
	if ctDict != None:
		editedCircuits = idle_protocol_crosstalk_experiment(ctDict)["edited_circuits"]
	elif circuits_override != None:
		editedCircuits = circuits_override
	print("length of editedCircuits: ", len(editedCircuits))
	for circuit in editedCircuits:
		if fixed_seed == None:
			randseed = np.random.randint(1, 10000)
		else:
			randseed = fixed_seed
		ds = pygsti.data.datasetconstruction.simulate_data(model, [circuit], num_samples=num_samples, sample_error='multinomial', seed=randseed, times=[0.0])
		dsList.append(ds)		# with low circuit lengths (<10) there might be duplicates in editedCircuits, which likely breaks later functionality
								# axel_crosstalk_detection_experiment2() checks for duplicates, but my idle_protocol_crosstalk_experiment(), which
								# edits the original circuits into editedCircuits, does not. Choose length > 10 and check that len(editedCircuits)
								# and len(list(dsDict.keys())) match before proceeding
	return dsList

def aggregate_simulated_idle_protocol_outcomes(ctDict, dsDict, protocol="xy"):
	"""
	Aggregates the simulated XY- or YZ-Idle protocol datasets into single-qubit spectator
	datasets inside the returned dictionary rdsDict.
	"""
	rdsDict = {}
	n = ctDict["spec"]["n"]
	# multiplier = ctDict["spec"]["multiplier"]
	cpl = ctDict["spec"]["cpl"] # circuits_per_length
	circuitList = ctDict["edited_circuits"]
	length = circuitList[0].depth
	singleQLabels = aggregate_labels(n, 1) # generates a dict of aggregated labels on the central qubit, see docs
	for qd in range(0, n): # driven qubit
		rdsDict[qd] = {}
		for i in range(qd*cpl, (qd+1)*cpl):
			multiqCircuit = circuitList[i]
			for qs in range(0, n):
				if qs != qd: # idles on spectators (qs != qd), which we are interested in
					idleCirc = Circuit(line_labels=[qs], editable=True, num_lines=1)
					for layerIndex in range(0, length):
						idleCirc = idleCirc.insert_layer(("id", qs), layerIndex) # generates an idle circuit on the central qubit
						# print("\n", layerIndex)
					if protocol == "yz": # detects y and z rotations
						idleCirc.insert_layer_inplace(("Gypi2", qs), 0) # ypi/2 rotation to start
						idleCirc.insert_layer_inplace(("Gypi2", qs), length-1) # end with another ypi/2
					idleCirc.done_editing()
					ds = dsDict[multiqCircuit]
					# print("ds: ", ds)
					dsAggre = pygsti.data.datasetconstruction.aggregate_dataset_outcomes(ds, singleQLabels[qs])
					sqtempDS = pygsti.data.DataSet(outcome_labels=["0","1"]) # empty single-qubit dataset
					dsRow = dsAggre[multiqCircuit] # aggregated counts as if measured on the central qubit only
					sqtempDS.add_count_dict(idleCirc, dsRow.counts)
					if idleCirc in rdsDict[qd]:
						rdsDict[qd][idleCirc].append(sqtempDS.copy()) # add single-qubit dataset to list of datasets if the list exists
					else:
						rdsDict[qd][idleCirc] = []
						rdsDict[qd][idleCirc].append(sqtempDS.copy())			
	return rdsDict

In [ ]:
# Generates the circuits for the XY-Idle protocol and exports them to files.
# Lumi used Qiskit version 1.1.2, and using a newer version caused mismatch between openqasm
# when attempting to transpile the circuits.
import pygsti
from pygsti.extras import ibmq
import qiskit
# %pip install qiskit==1.1.2
from qiskit import QuantumCircuit
from qiskit import qpy
import pickle
from pygsti.circuits import Circuit

helmiConnectivity = [(2,0), (2,1), (2,3), (2,4)]

helmiGeometry = pygsti.baseobjs.qubitgraph.QubitGraph([0,1,2,3,4], initial_edges=helmiConnectivity, directed=False)
# print(helmiGeometry.edges())

helmiProcessorSpec = pygsti.processors.QubitProcessorSpec(5, ["Gxpi2", "Gypi2", "Gzpi2", "Gi"], geometry = helmiGeometry)

gates_available = list(helmiProcessorSpec.primitive_op_labels)
# print(gates_available)
length = 20
circuits_per_length = 20
ctDict = axel_crosstalk_detection_experiment2(helmiProcessorSpec, [length], circuits_per_length, 20, verbosity=0, multiplier=1, idle_prob=0)

# circuitList = list(ctDict["circuits"].values())
editedCircuits = idle_protocol_crosstalk_experiment(ctDict, protocol="xy")["edited_circuits"]

for circuit in editedCircuits:
    print("\n", circuit)

circuits_to_quantumcircuits(ctDict, circuit_list=editedCircuits)

[(0, 2), (1, 2), (2, 3), (2, 4)]
((0,), (1,), (2,), (3,), (4,))
[Label(('Gxpi2', 0)), Label(('Gxpi2', 1)), Label(('Gxpi2', 2)), Label(('Gxpi2', 3)), Label(('Gxpi2', 4)), Label(('Gypi2', 0)), Label(('Gypi2', 1)), Label(('Gypi2', 2)), Label(('Gypi2', 3)), Label(('Gypi2', 4)), Label(('Gzpi2', 0)), Label(('Gzpi2', 1)), Label(('Gzpi2', 2)), Label(('Gzpi2', 3)), Label(('Gzpi2', 4)), Label(('Gi', 0)), Label(('Gi', 1)), Label(('Gi', 2)), Label(('Gi', 3)), Label(('Gi', 4)), Label(('Gcnot', 0, 2)), Label(('Gcnot', 1, 2)), Label(('Gcnot', 2, 0)), Label(('Gcnot', 2, 1)), Label(('Gcnot', 2, 3)), Label(('Gcnot', 2, 4)), Label(('Gcnot', 3, 2)), Label(('Gcnot', 4, 2))]
cnt: 100

 Qubit 0 ---|Gzpi2|-|Gzpi2|-|Gypi2|-|Gxpi2|-|Gxpi2|-|Gzpi2|-|Gypi2|-|Gi|-|Gypi2|-|Gypi2|-|Gzpi2|-|Gzpi2|-|Gypi2|-|Gzpi2|-|Gi|-|Gi|-|Gi|-|Gxpi2|-|Gypi2|-|Gzpi2|---
Qubit 1 ---|     |-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|  |-|  |-|     |-|     |-|     |---
Qub

In [ ]:
# --- EXPERIMENTAL DATA
# XY-Idle protocol
import pickle

def counts_in(file):
    with open(file, 'rb') as f:
        return pickle.load(f)

length = 20
results = {}
totalCount = 0
globalSignificance = 0.05
for q in range(0, 5): # q is the driven qubit
	print("-----\n")
	fileName = "exported_counts_q" + str(q)
	countsList = counts_in(fileName)
	rdsDict = aggregate_experimental_idle_protocol_outcomes(countsList, length, (q,), num_qubits=5, protocol="xy")
	comparatorDict = compare_datasets(rdsDict)
	centralCircuits = list(comparatorDict.keys())
	for circuit in centralCircuits:
		count = 0
		tvdsum = 0.0
		avtvd = 0.0
		minp = 1.0
		maxtvd = 0.0
		maxstd = 0.0
		worstDsPair = comparatorDict[circuit]["ds_pairs"][0]
		print("-----\n\n\n\n\n\n")
		print("-----\nDriven qubit is q%d..."%q, "\nSpectator/central circuit: ", circuit)
		print("\ndatasets to compare pairwise: ", len(rdsDict[circuit]))
		pairwiseComparisons = len(comparatorDict[circuit]["comparators"])
		correctedSignificance = globalSignificance/pairwiseComparisons # must correct because more comparisons lead to more false crosstalk flags otherwise
		for j in range(0, pairwiseComparisons):
			count += 1
			totalCount += 1
			print("")
			print(totalCount)
			for ds in comparatorDict[circuit]["ds_pairs"][j]:
				print(ds)
			# comparatorDict[circuit][j].run(significance=0.05, verbosity=1)
			comparatorDict[circuit]["comparators"][j].run(correctedSignificance, verbosity=1, aggregate_test_weighting=0)
			# pygsti.report.workspaceplots.DatasetComparisonHistogramPlot(w, comparatorDict[centralCircuits[i]][j]).display()
			tvd = comparatorDict[circuit]["comparators"][j].tvd(circuit)
			tvdsum += tvd
			print("TVD: ",tvd)
			if tvd != None and tvd > maxtvd:
				maxtvd = tvd
			pvalue = comparatorDict[circuit]["comparators"][j].pvalue(circuit)
			if pvalue < minp:
				minp = pvalue
				worstDsPair = comparatorDict[circuit]["ds_pairs"][j]
			print("pvalue: ", pvalue)
			nsigma = comparatorDict[circuit]["comparators"][j].aggregate_nsigma
			if nsigma > maxstd:
				maxstd = nsigma
			print("Standard deviations: ", nsigma)
		avtvd = tvdsum/count
		crosstalkFlag = False
		if minp <= correctedSignificance:
			crosstalkFlag = True
		spectator = list(circuit.line_labels)[0]
		results[(q, spectator)] = (minp, maxtvd, avtvd, maxstd, crosstalkFlag, circuit, worstDsPair)
		print("\n\n-----\n")
		print("--- Driving Q",str(q),", with Q",str(spectator)," spectating ---")
		print("min p: ", minp)
		print("maxTVD: ", maxtvd)
		print("average TVD: ", avtvd)
		print("max stds: ", maxstd)
		print("Crosstalk detected: ", crosstalkFlag)
		print("Least consistent datasets:")
		for ds in worstDsPair:
			print(ds[circuit])

-----

-----






-----
Driven qubit is q0... 
Spectator/central circuit:  Qubit 1 ---|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|---


datasets to compare pairwise:  20

1
id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1@(1)  :  {('0',): 948.0, ('1',): 52.0}


id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1@(1)  :  {('0',): 956.0, ('1',): 44.0}


Statistical hypothesis tests did NOT find inconsistency between the data at 0.03% significance.
TVD:  0.008000000000000004
pvalue:  0.4024297724638486
Standard deviations:  -0.21138676697220593

2
id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1@(1)  :  {('0',): 948.0, ('1',): 52.0}


id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1id:1@(1)  :  {('0',): 951.0, ('1',): 49.0}


Statistical hypothesis tests did NOT find inconsistency between the data at 0.03% signific

In [ ]:
# Generates more clear results outputs
resultKeys = list(results.keys())
for key in resultKeys:
	print("Driven qubit:    q"+str(key[0]))
	print("Spectator qubit: q"+str(key[1]))
	print("Min p: ", results[key][0])
	print("Max TVD: ", results[key][1])
	print("Average TVD: ", results[key][2])
	print("Max stds: ", results[key][3])
	print("Crosstalk detected: @@@", results[key][4],"@@@")
	print("Least consistent datasets:")
	for ds in results[key][6]:
		print(ds[results[key][5]])
	print("-----\n")

Driven qubit:    q0
Spectator qubit: q1
Min p:  0.03653907871201978
Max TVD:  0.019000000000000006
Average TVD:  0.006194736842105264
Max stds:  2.384199465078516
Crosstalk detected: @@@ False @@@
Least consistent datasets:
{('0',): 947.0, ('1',): 53.0}
{('0',): 966.0, ('1',): 34.0}
-----

Driven qubit:    q0
Spectator qubit: q2
Min p:  0.010324465274603511
Max TVD:  0.02300000000000001
Average TVD:  0.007726315789473675
Max stds:  3.9442682476243967
Crosstalk detected: @@@ False @@@
Least consistent datasets:
{('0',): 969.0, ('1',): 31.0}
{('0',): 946.0, ('1',): 54.0}
-----

Driven qubit:    q0
Spectator qubit: q3
Min p:  7.338111824850557e-06
Max TVD:  0.03600000000000002
Average TVD:  0.00958947368421051
Max stds:  13.507867531081297
Crosstalk detected: @@@ True @@@
Least consistent datasets:
{('0',): 947.0, ('1',): 53.0}
{('0',): 983.0, ('1',): 17.0}
-----

Driven qubit:    q0
Spectator qubit: q4
Min p:  0.043425426534568046
Max TVD:  0.013000000000000006
Average TVD:  0.0038789473

In [ ]:
# Modifies the XY-Idle circuits into the YZ-version without randomizing new driven circuits
editedCircuitsYZ = idle_protocol_crosstalk_experiment(ctDict, protocol="yz")["edited_circuits"]

for circuit in editedCircuitsYZ:
    print("\n", circuit)

circuits_to_quantumcircuits(ctDict, circuit_list=editedCircuitsYZ, file_name="exported_circuitsYZ_q")


 Qubit 0 ---|Gzpi2|-|Gzpi2|-|Gypi2|-|Gxpi2|-|Gxpi2|-|Gzpi2|-|Gypi2|-|Gi|-|Gypi2|-|Gypi2|-|Gzpi2|-|Gzpi2|-|Gypi2|-|Gzpi2|-|Gi|-|Gi|-|Gi|-|Gxpi2|-|Gypi2|-|Gzpi2|---
Qubit 1 ---|Gypi2|-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|  |-|  |-|     |-|     |-|Gypi2|---
Qubit 2 ---|Gypi2|-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|  |-|  |-|     |-|     |-|Gypi2|---
Qubit 3 ---|Gypi2|-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|  |-|  |-|     |-|     |-|Gypi2|---
Qubit 4 ---|Gypi2|-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|     |-|     |-|     |-|     |-|     |-|     |-|  |-|  |-|  |-|     |-|     |-|Gypi2|---


 Qubit 0 ---|Gxpi2|-|Gzpi2|-|Gzpi2|-|Gxpi2|-|Gi|-|Gypi2|-|Gxpi2|-|Gxpi2|-|Gypi2|-|Gypi2|-|Gypi2|-|Gzpi2|-|Gi|-|Gxpi2|-|Gi|-|Gypi2|-|Gzpi2|-|Gi|-|Gypi2|-|Gxpi2|---
Qubit 1 ---|Gypi2|-|   

In [ ]:
# --- EXPERIMENTAL DATA
# YZ-Idle protocol
def counts_in(file):
    with open(file, 'rb') as f:
        return pickle.load(f)
	
resultsYZ = {}
totalCountYZ = 0
globalSignificanceYZ = 0.05
for q in range(0, 5): # q is the driven qubit
	print("-----\n")
	fileName = "exported_countsYZ_q" + str(q)
	countsList = counts_in(fileName)
	rdsDict = aggregate_experimental_idle_protocol_outcomes(countsList, length, (q,), num_qubits=5, protocol="yz")
	comparatorDict = compare_datasets(rdsDict)
	centralCircuits = list(comparatorDict.keys())
	for circuit in centralCircuits:
		count = 0
		tvdsum = 0.0
		avtvd = 0.0
		minp = 1.0
		maxtvd = 0.0
		maxstd = 0.0
		worstDsPair = comparatorDict[circuit]["ds_pairs"][0]
		print("-----\n\n\n\n\n\n")
		print("-----\nDriven qubit is q%d..."%q, "\nSpectator/central circuit: ", circuit)
		print("\ndatasets to compare pairwise: ", len(rdsDict[circuit]))
		pairwiseComparisons = len(comparatorDict[circuit]["comparators"])
		print(pairwiseComparisons)
		correctedSignificance = globalSignificanceYZ/pairwiseComparisons # must correct because more comparisons lead to more false crosstalk flags otherwise
		for j in range(0, pairwiseComparisons):
			count += 1
			totalCountYZ += 1
			print("")
			print(totalCountYZ)
			for ds in comparatorDict[circuit]["ds_pairs"][j]:
				print(ds)
			# comparatorDict[circuit][j].run(significance=0.05, verbosity=1)
			comparatorDict[circuit]["comparators"][j].run(correctedSignificance, verbosity=1, aggregate_test_weighting=0)
			# pygsti.report.workspaceplots.DatasetComparisonHistogramPlot(w, comparatorDict[centralCircuits[i]][j]).display()
			tvd = comparatorDict[circuit]["comparators"][j].tvd(circuit)
			tvdsum += tvd
			print("TVD: ",tvd)
			if tvd != None and tvd > maxtvd:
				maxtvd = tvd
			pvalue = comparatorDict[circuit]["comparators"][j].pvalue(circuit)
			if pvalue < minp:
				minp = pvalue
				worstDsPair = comparatorDict[circuit]["ds_pairs"][j]
			print("pvalue: ", pvalue)
			nsigma = comparatorDict[circuit]["comparators"][j].aggregate_nsigma
			if nsigma > maxstd:
				maxstd = nsigma
			print("Standard deviations: ", nsigma)
		avtvd = tvdsum/count
		crosstalkFlag = False
		if minp <= correctedSignificance:
			crosstalkFlag = True
		spectator = list(circuit.line_labels)[0]
		resultsYZ[(q, spectator)] = (minp, maxtvd, avtvd, maxstd, crosstalkFlag, circuit, worstDsPair)
		print("\n\n-----\n")
		print("--- Driving Q",str(q),", with Q",str(spectator)," spectating ---")
		print("min p: ", minp)
		print("maxTVD: ", maxtvd)
		print("average TVD: ", avtvd)
		print("max stds: ", maxstd)
		print("Crosstalk detected: ", crosstalkFlag)
		print("Least consistent datasets:")
		for ds in worstDsPair:
			print(ds[circuit])

-----

-----






-----
Driven qubit is q0... 
Spectator/central circuit:  Qubit 1 ---|Gypi2|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|id|-|Gypi2|---


datasets to compare pairwise:  20
190

1
Gypi2:1id:1id:1id:1id:1id:1id:1id:1id:1Gypi2:1@(1)  :  {('0',): 477.0, ('1',): 523.0}


Gypi2:1id:1id:1id:1id:1id:1id:1id:1id:1Gypi2:1@(1)  :  {('0',): 486.0, ('1',): 514.0}


Statistical hypothesis tests did NOT find inconsistency between the data at 0.03% significance.
TVD:  0.009000000000000008
pvalue:  0.6871168716804239
Standard deviations:  -0.5923968876848047

2
Gypi2:1id:1id:1id:1id:1id:1id:1id:1id:1Gypi2:1@(1)  :  {('0',): 477.0, ('1',): 523.0}


Gypi2:1id:1id:1id:1id:1id:1id:1id:1id:1Gypi2:1@(1)  :  {('0',): 496.0, ('1',): 504.0}


Statistical hypothesis tests did NOT find inconsistency between the data at 0.03% significance.
TVD:  0.019000000000000017
pvalue:  0.39530207692564345
Standard deviations:  -0.19617238044474666

3
Gypi2:1id:1id:1id:1id:1id:1id:1id:1id:1Gypi2:1@(1)  :  {('0',): 4

In [7]:
resultKeysYZ = list(resultsYZ.keys())
for key in resultKeysYZ:
	print("Driven qubit:    q"+str(key[0]))
	print("Spectator qubit: q"+str(key[1]))
	print("Min p: ", resultsYZ[key][0])
	print("Max TVD: ", resultsYZ[key][1])
	print("Average TVD: ", resultsYZ[key][2])
	print("Max stds: ", resultsYZ[key][3])
	print("Crosstalk detected: @@@", resultsYZ[key][4],"@@@")
	print("Least consistent datasets:")
	for ds in resultsYZ[key][6]:
		print(ds[resultsYZ[key][5]])
	print("-----\n")

Driven qubit:    q0
Spectator qubit: q1
Min p:  0.0
Max TVD:  0.19300000000000003
Average TVD:  0.04697368421052632
Max stds:  53.25931409973522
Crosstalk detected: @@@ True @@@
Least consistent datasets:
{('0',): 338.0, ('1',): 662.0}
{('0',): 529.0, ('1',): 471.0}
-----

Driven qubit:    q0
Spectator qubit: q2
Min p:  0.0
Max TVD:  0.209
Average TVD:  0.05713684210526313
Max stds:  67.72554008857632
Crosstalk detected: @@@ True @@@
Least consistent datasets:
{('0',): 725.0, ('1',): 275.0}
{('0',): 543.0, ('1',): 457.0}
-----

Driven qubit:    q0
Spectator qubit: q3
Min p:  4.460874706291307e-07
Max TVD:  0.10900000000000004
Average TVD:  0.025194736842105263
Max stds:  17.312739372825014
Crosstalk detected: @@@ True @@@
Least consistent datasets:
{('0',): 682.0, ('1',): 318.0}
{('0',): 573.0, ('1',): 427.0}
-----

Driven qubit:    q0
Spectator qubit: q4
Min p:  4.701794509287538e-13
Max TVD:  0.138
Average TVD:  0.03197368421052633
Max stds:  36.29266979378651
Crosstalk detected: @@@

In [ ]:
#--- SIMULATED CNOT-YZ
import pygsti
import random
from pygsti.circuits import Circuit

helmiConnectivity = [(2,0), (2,1), (2,3), (2,4)]
helmiGeometry = pygsti.baseobjs.qubitgraph.QubitGraph([0,1,2,3,4], initial_edges=helmiConnectivity, directed=False)
print(helmiGeometry.edges())

helmiProcessorSpec = pygsti.processors.QubitProcessorSpec(5, ["Gxpi2", "Gypi2", "Gzpi2", "Gi", "Gcnot"], geometry = helmiGeometry)

mdlCn = pygsti.models.create_cloud_crosstalk_model(helmiProcessorSpec,
	depolarization_strengths={
	"Gypi2": 0.001,
	("Gcnot", 2,0): {(1,): 0.05, (3,): 0.025, (4,): 0.001},
	("Gcnot", 2,1): {(0,): 0.0005}},
	simulator="auto"
)

def cnot_protocol(num_qubits, connectivity_list, length, variants):
	"""
	Implements the CNOT benchmarking protocol described in section 4.8 of my thesis
	"Device-agnostic crosstalk detection in quantum computers". Generates a dictionary
	where each key is the driven qubit pair (control, target) and its value is a list
	of circuits where an ascending number of CNOTs is applied on those qubits on random
	layers.
	"""
	circuitDict = {}
	layerIndexPool = list(range(0,length))
	for pair in connectivity_list:
		# pList = list(pair)
		# print(pair)
		baseCircuit = Circuit(num_lines=num_qubits, line_labels=list(range(0,num_qubits)), editable=True)
		baseCircuit.insert_idling_layers_inplace(insert_before=None, num_to_insert=length, lines=None) # generates a length=length idle circuit
		for i in range(0,num_qubits):
			baseCircuit[0, i] = ("Gypi2", i)
			baseCircuit[length-1, i] = ("Gypi2", i)
		baseCircuit1 = baseCircuit.copy(editable=True)
		baseCircuit2 = baseCircuit.copy(editable=True)
		revPair = tuple(reversed(pair))
		circuitDict[pair] = []
		circuitDict[revPair] = []
		for l in range(0,length):
			baseCircuit1[l, pair[0]] = ("Gzpi2", pair[0])
			baseCircuit2[l, revPair[0]] = ("Gzpi2", revPair[0])
		for var in range(0,variants):
			tempCircuit1 = baseCircuit1.copy(editable=True)
			random.shuffle(layerIndexPool)
			ind = layerIndexPool[:var+1] # picks first var+1 indices from the shuffled index list
			# print(ind)
			for layer in ind:
				tempCircuit1[layer, pair] = ("Gcnot", pair[0], pair[1])	
			tempCircuit1.done_editing()
			circuitDict[pair].append(tempCircuit1)
			# print("appended\n", tempCircuit1)
			tempCircuit2 = baseCircuit2.copy(editable=True)
			ind = []
			random.shuffle(layerIndexPool)
			ind = layerIndexPool[:var+1] # picks first var+1 indices from the shuffled index list
			for layer in ind:
				tempCircuit2[layer, revPair] = ("Gcnot", revPair[0], revPair[1])
			tempCircuit2.done_editing()
			circuitDict[revPair].append(tempCircuit2)
			# print("appended\n", tempCircuit2)
			
	return circuitDict
		
def aggregate_simulated_cnot_protocol_outcomes(ds_list, num_qubits=5, driven_qubits_tuple=None, protocol="xy"):
	"""
	Aggregates the simulated CNOT benchmarking protocol datasets into single-qubit spectator
	qubit datasets. Returns a dictionary where each key is a spectator circuit and its value
	a list of datasets.
	"""
	dQubits = list(driven_qubits_tuple)
	circuitList = []
	for ds in ds_list:
		# print(ds)
		key = list(ds.keys())[0]
		circuitList.append(key)
	
	rdsDict = {}
	length = circuitList[0].depth
	print("length: ", length)
	singleQLabels = aggregate_labels(num_qubits, 1) # generates a dict of aggregated labels on the central qubit, see docs

	for i, ds in enumerate(ds_list):
		for qs in range(0, num_qubits): # spectator qubit
			if qs not in dQubits: # idles on spectators, which we are interested in
				idleCirc = Circuit(line_labels=[qs], editable=True, num_lines=1)
				idleCirc.insert_idling_layers_inplace(insert_before=None, num_to_insert=length, lines=None) # generates a length=length idle circuit

				if protocol == "yz": # detects y and z rotations
					idleCirc[0] = ("Gypi2", qs) # ypi/2 rotation to start
					idleCirc[length-1] = ("Gypi2", qs) # end with another ypi/2
				idleCirc.done_editing()
				dsAggre = pygsti.data.datasetconstruction.aggregate_dataset_outcomes(ds, singleQLabels[qs])
				sqtempDS = pygsti.data.DataSet(outcome_labels=["0","1"]) # empty single-qubit dataset
				dsRow = dsAggre[circuitList[i]] # aggregated counts as if measured on the central qubit only
				sqtempDS.add_count_dict(idleCirc, dsRow.counts)

				if idleCirc in rdsDict:
					rdsDict[idleCirc].append(sqtempDS.copy()) # add single-qubit dataset to list of datasets if the list exists
				else:
					rdsDict[idleCirc] = []
					rdsDict[idleCirc].append(sqtempDS.copy())		
	return rdsDict

circuitDict = cnot_protocol(5, helmiConnectivity, 10, 5)
# circuitDict = cnot_protocol(5, helmiConnectivity, 20, 10)

pairList = helmiConnectivity + [tuple(reversed(pair)) for pair in helmiConnectivity] # runs CNOTs also with flipped (control, target)
print(pairList)
# print(circuitDict[helmiConnectivity[0]])

[(0, 2), (1, 2), (2, 3), (2, 4)]
[(2, 0), (2, 1), (2, 3), (2, 4), (0, 2), (1, 2), (3, 2), (4, 2)]


In [ ]:
#--- SIMULATED CNOT-YZ DATA
resultsCYZ = {}
totalCountCYZ = 0
globalSignificanceCYZ = 0.05
for pair in pairList: # pair is the driven qubit tuple
	print("-----\n")
	dsList = idle_protocol_crosstalk_simulation(mdlCn, ctDict=None, circuits_override=circuitDict[pair], num_samples=10000, fixed_seed=None) # choose number of samples here
	rdsDict = aggregate_simulated_cnot_protocol_outcomes(dsList, num_qubits=5, driven_qubits_tuple=pair, protocol="yz")

	comparatorDict = compare_datasets(rdsDict)
	centralCircuits = list(comparatorDict.keys())

	for circuit in centralCircuits:
		# print("circuit: ", circuit)
		count = 0
		tvdsum = 0.0
		avtvd = 0.0
		minp = 1.0
		maxtvd = 0.0
		maxstd = 0.0
		worstDsPair = comparatorDict[circuit]["ds_pairs"][0]
		print("-----\n\n\n\n\n\n")
		print("-----\nDriven qubits are ",pair,"...", "\nSpectator/central circuit: ", circuit)
		print("\ndatasets to compare pairwise: ", len(rdsDict[circuit]))
		pairwiseComparisons = len(comparatorDict[circuit]["comparators"])
		print(pairwiseComparisons)
		correctedSignificance = globalSignificanceCYZ/pairwiseComparisons # must correct because more comparisons lead to more false crosstalk flags otherwise
		for j in range(0, pairwiseComparisons):
			count += 1
			totalCountCYZ += 1
			print("")
			print(totalCountCYZ)
			for ds in comparatorDict[circuit]["ds_pairs"][j]:
				print(ds)
			# comparatorDict[circuit][j].run(significance=0.05, verbosity=1)
			comparatorDict[circuit]["comparators"][j].run(correctedSignificance, verbosity=1, aggregate_test_weighting=0)
			# pygsti.report.workspaceplots.DatasetComparisonHistogramPlot(w, comparatorDict[centralCircuits[i]][j]).display()
			tvd = comparatorDict[circuit]["comparators"][j].tvd(circuit)
			tvdsum += tvd
			print("TVD: ",tvd)
			if tvd != None and tvd > maxtvd:
				maxtvd = tvd
			pvalue = comparatorDict[circuit]["comparators"][j].pvalue(circuit)
			if pvalue < minp:
				minp = pvalue
				worstDsPair = comparatorDict[circuit]["ds_pairs"][j]
			print("pvalue: ", pvalue)
			nsigma = comparatorDict[circuit]["comparators"][j].aggregate_nsigma
			if nsigma > maxstd:
				maxstd = nsigma
			print("Standard deviations: ", nsigma)
		avtvd = tvdsum/count
		crosstalkFlag = False
		if minp <= correctedSignificance:
			crosstalkFlag = True
		spectator = list(circuit.line_labels)[0]
		resultsCYZ[(pair, spectator)] = (minp, maxtvd, avtvd, maxstd, crosstalkFlag, circuit, worstDsPair)
		print("\n\n-----\n")
		print("--- Driving qubits ",pair,", with Q",str(spectator)," spectating ---")
		print("min p: ", minp)
		print("maxTVD: ", maxtvd)
		print("average TVD: ", avtvd)
		print("max stds: ", maxstd)
		print("Crosstalk detected: ", crosstalkFlag)
		print("Least consistent datasets:")
		for ds in worstDsPair:
			print(ds[circuit])

-----

length of editedCircuits:  5
length:  10
-----






-----
Driven qubits are  (2, 0) ... 
Spectator/central circuit:  Qubit 1 ---|Gypi2|-| |-| |-| |-| |-| |-| |-| |-| |-|Gypi2|---


datasets to compare pairwise:  5
10

1
Gypi2:1[][][][][][][][]Gypi2:1@(1)  :  {('0',): 343.0, ('1',): 9657.0}


Gypi2:1[][][][][][][][]Gypi2:1@(1)  :  {('0',): 666.0, ('1',): 9334.0}


The data are INCONSISTENT at 0.50% significance.
  - Details:
    - The aggregate log-likelihood ratio test is significant at 77.59 standard deviations.
    - The aggregate log-likelihood ratio test standard deviations signficance threshold is inf
    - The number of sequences with data that is inconsistent is 1
    - The maximum SSTVD over all sequences is 0.03
TVD:  0.0323
pvalue:  0.0
Standard deviations:  77.59428791683932

2
Gypi2:1[][][][][][][][]Gypi2:1@(1)  :  {('0',): 343.0, ('1',): 9657.0}


Gypi2:1[][][][][][][][]Gypi2:1@(1)  :  {('0',): 907.0, ('1',): 9093.0}


The data are INCONSISTENT at 0.50% significanc

In [ ]:
# Generates more clear results outputs
resultKeysCYZ = list(resultsCYZ.keys())
for key in resultKeysCYZ:
	print("Driven qubits:  "+str(key[0]))
	print("Spectator qubit: q"+str(key[1]))
	print("Min p: ", resultsCYZ[key][0])
	print("Max TVD: ", resultsCYZ[key][1])
	print("Average TVD: ", resultsCYZ[key][2])
	print("Max stds: ", resultsCYZ[key][3])
	print("Crosstalk detected: @@@", resultsCYZ[key][4],"@@@")
	print("Least consistent datasets:")
	for ds in resultsCYZ[key][6]:
		print(ds[resultsCYZ[key][5]])
	print("-----\n")

Driven qubits:  (2, 0)
Spectator qubit: q1
Min p:  0.0
Max TVD:  0.11629999999999999
Average TVD:  0.05725999999999999
Max stds:  610.3164159592934
Crosstalk detected: @@@ True @@@
Least consistent datasets:
{('0',): 343.0, ('1',): 9657.0}
{('0',): 666.0, ('1',): 9334.0}
-----

Driven qubits:  (2, 0)
Spectator qubit: q3
Min p:  0.0
Max TVD:  0.0665
Average TVD:  0.033499999999999995
Max stds:  352.4646863698226
Crosstalk detected: @@@ True @@@
Least consistent datasets:
{('0',): 173.0, ('1',): 9827.0}
{('0',): 471.0, ('1',): 9529.0}
-----

Driven qubits:  (2, 0)
Spectator qubit: q4
Min p:  0.00033486436461860336
Max TVD:  0.0026999999999999624
Average TVD:  0.0014199999999999883
Max stds:  8.389507892587197
Crosstalk detected: @@@ True @@@
Least consistent datasets:
{('0',): 16.0, ('1',): 9984.0}
{('0',): 43.0, ('1',): 9957.0}
-----

Driven qubits:  (2, 1)
Spectator qubit: q0
Min p:  0.0748116445135365
Max TVD:  0.0011999999999999893
Average TVD:  0.0006199999999999992
Max stds:  1.537